# Tahiti or Hawaii
The goal of this notebook is to train a deep learning algorithm to identify whether or not a picture is of Tahiti or Hawaii.

## Libraries
We will be using the `fastai` and `fastbook` libraries

In [1]:
!pip install -Uqq fastai

In [2]:
!pip install -Uqq fastbook

In [3]:
!pip install timm==0.6.2dev0

^C
ERROR: Operation cancelled by user


In [4]:
import timm

KeyboardInterrupt: 

In [ ]:
import fastbook
fastbook.setup_book()

Load `fastai.vision.widgets` to collect and work with images from Bing

In [ ]:
from fastbook import *
from fastai.vision.widgets import *

Use Bing Search API key to grant access to Bing Search tools

In [ ]:
key = os.environ.get('AZURE_SEARCH_KEY', 'a073c5bc49dd4450b17d272d68207d80')

Check is notebook is able to search Bing

In [ ]:
search_images_bing

## Data

### Data Types
Define the three data types:
1. Tahiti
2. Hawaii
3. Island *(not Tahiti and not Hawaii)*

In [ ]:
#island_types = 'tahiti','hawaii','island -tahiti -hawaii'
searches = 'tahiti', 'hawaii'
path = Path('islands')

### Collect Data
Search Bing for the three defined data types.\
Save the images to folders that use their identity as their path alias

In [ ]:
## Using Bring
#if not path.exists():
#    path.mkdir()
#    for o in island_types:
#        dest = (path/o)
#        dest.mkdir(exist_ok=True)
#        results = search_images_bing(key, f'{o}')
#        download_images(dest, urls=results.attrgot('contentUrl'))

In [ ]:
## Using DuckDuckGo
def search_images(term, max_images=200):
    url = 'https://duckduckgo.com/'
    res = urlread(url,data={'q':term})
    searchObj = re.search(r'vqd=([\d-]+)\&', res)
    requestUrl = url + 'i.js'
    params = dict(l='us-en', o='json', q=term, vqd=searchObj.group(1), f=',,,', p='1', v7exp='a')
    urls,data = set(),{'next':1}
    while len(urls)<max_images and 'next' in data:
        data = urljson(requestUrl,data=params)
        urls.update(L(data['results']).itemgot('image'))
        requestUrl = url + data['next']
        time.sleep(0.2)
    return L(urls)[:max_images]

In [ ]:
## Using DuckDuckGo
#for o in searches:
#    dest = (path/o)
#    dest.mkdir(exist_ok=True, parents=True)
#    download_images(dest, urls=search_images(f'{o} photo'))
#    resize_images(path/o, max_size=400, dest=path/o)

Confirm that images were downloaded

In [ ]:
fns = get_image_files(path)
fns

### Remove Bad Data
Check for corrupt files

In [ ]:
failed = verify_images(fns)
failed

Unlink All failed images

In [ ]:
failed.map(Path.unlink);

## Train Model
Create and train model on the three collections of images.\
Create two collections of data (`splitter=RandomSplitter(valid_pct=0.2, seed=42)`):
1. Use 80% for training the model  
2. Save 20% for testing the model
Each image has a label of `parent_label` which represents their parent path name.  


In [ ]:
islands = DataBlock(
    blocks=(ImageBlock, CategoryBlock), 
    get_items=get_image_files, 
    splitter=RandomSplitter(valid_pct=0.8, seed=42),
    get_y=parent_label,
    item_tfms=Resize(128))

In [ ]:
dls = islands.dataloaders(path)

In [ ]:
dls.valid.show_batch(max_n=4, nrows=1)

### Data Augmentation
We don't have a lot of data for our problem (less than 150 pictures of each collection), so to train our model, we'll use `RandomResizedCrop` with an image size of 224 px, which is fairly standard for image classification, and default `aug_transforms`:

In [ ]:
## Remove Data augmentation for DuckDuckGo version
islands = islands.new(
    item_tfms=RandomResizedCrop(224, min_scale=0.5),
    batch_tfms=aug_transforms())
dls = islands.dataloaders(path)

#### Data Augmentation Example
Here is an example of a single image being used to create 8 data points via data augmentation:

In [ ]:
dls.train.show_batch(max_n=8, nrows=2, unique=True)

#### Create Learner
We can now create our `Learner` and fine-tune it in the usual way:

### Check Results

In [ ]:
#learn = vision_learner(dls, resnet18, metrics=error_rate)
## using 34 for DUckDuckGo bc island categorization sucks with 18
#learn = vision_learner(dls, resnet34, metrics=error_rate)
#learn.fine_tune(4)
learn = vision_learner(dls, 'convnext_base_in22ft1k', metrics=error_rate, loss_func=CrossEntropyLossFlat())
learn.fine_tune(4)

#### Confusion Matrix
Here we create a confusion matrix to see where categories have been:\
1. Categorized correctly (Along the diagonal)
OR
2. One category was incorrectly predicted as another category

In [ ]:
interp = ClassificationInterpretation.from_learner(learn)
interp.plot_confusion_matrix()

#### Inspect Loss
The loss is a number that is higher if the model is incorrect (especially if it's also confident of its incorrect answer), or if it's correct, but not confident of its correct answer.\
`plot_top_losses` shows us the images with the highest loss in our dataset.

In [ ]:
interp.plot_top_losses(5, nrows=1)

#### Cleaning Data
fastai includes a handy GUI for data cleaning called `ImageClassifierCleaner` that allows you to choose a category and the training versus validation set and view the highest-loss images (in order), along with menus to allow images to be selected for removal or relabeling:

In [ ]:
#hide_output
cleaner = ImageClassifierCleaner(learn)
cleaner

`ImageClassifierCleaner` doesn't actually do the deleting or changing of labels for you; it just returns the indices of items to change. So, for instance, to delete (`unlink`) all images selected for deletion, we would run:

```python
for idx in cleaner.delete(): cleaner.fns[idx].unlink()
```

To move images for which we've selected a different category, we would run:

```python
for idx,cat in cleaner.change(): shutil.move(str(cleaner.fns[idx]), path/cat)
```

In [ ]:
#hide
#for idx in cleaner.delete(): cleaner.fns[idx].unlink()
#for idx,cat in cleaner.change(): shutil.move(str(cleaner.fns[idx]), path/cat)

## Export Model
When you call `export`, fastai will save a file called "export.pkl":

In [ ]:
learn.export('convnext-model.pkl')

check that the file exists, by using the `ls` method that fastai adds to Python's `Path` class:

In [ ]:
path = Path()
path.ls(file_exts='.pkl')

### Create App.py

In [ ]:
# nbdev requires jupyter, but we're already in a notebook environment, so we can install without dependencies
##!pip install -U --no-deps 'nbdev<2' fastcore

In [ ]:
##import nbdev
##nbdev.__version__

#### Export app.ipynb

In [ ]:
##%notebook -e app.ipynb